In [1]:
import sys
import csv
import matplotlib.pyplot as plt
import jax.numpy as np
import mayavi as maya
from mayavi import mlab
import tables as tb
#%gui qt
#%matplotlib notebook
mlab.init_notebook('x3d',800,800)
#mlab.init_notebook()
#%matplotlib widget
#mlab.options.offscreen = True

Notebook initialized with x3d backend.


In [2]:
def draw_surface(r):
    r = np.concatenate((r, r[0:, :, :]), axis=0)
    r = np.concatenate((r, r[:, 0:, :]), axis=1)
    x = r[:,:,0]
    y = r[:,:,1]
    z = r[:,:,2]
    p = mlab.mesh(x,y,z,color=(0.8,0.0,0.0))
    return p

def draw_coils(r):
    for ic in range(r.shape[0]):
        p = mlab.plot3d(r[ic,:,0], r[ic,:,1], r[ic,:,2], tube_radius = 0.004, line_width = 0.01, color = (0.0, 0.0, 0.8))
    return p
def draw_coils_c(r, c= (0.0, 0.0, 0.8)):
    for ic in range(r.shape[0]):
        p = mlab.plot3d(r[ic,:,0], r[ic,:,1], r[ic,:,2], tube_radius = 0.004, line_width = 0.01, color = c)
    return p
def r(fc, theta):
    r = np.zeros((3, fc.shape[1], 32 + 1))
    for m in range(fc.shape[2]):
        r += fc[:3, :, None, m] * np.cos(m * theta)[None, None, :] + fc[3:, :, None, m] * np.sin(m * theta)[None, None, :]
    return np.transpose(r, (1, 2, 0))

In [3]:

sg = np.load("sg.npy")
r_surf = np.load("r_surf.npy")
with tb.open_file("coils.hdf5", "r") as f:
    fc = np.asarray(f.root.coilSeries[:, :, :])
theta = np.linspace(0, 2 * np.pi, 32 + 1)
l = r(fc, theta)

/opt/conda/lib/python3.8/site-packages/jax/lib/xla_bridge.py:130: UserWarning: No GPU/TPU found, falling back to CPU.
  warnings.warn('No GPU/TPU found, falling back to CPU.')


In [4]:
mlab.clf()
p = draw_surface(r_surf)
p = draw_coils(l)
p

In [5]:
sys.version

'3.8.4 | packaged by conda-forge | (default, Jul 17 2020, 15:16:46) \n[GCC 7.5.0]'

In [10]:
with tb.open_file("coils_final.hdf5", "r") as f:
    fc = np.asarray(f.root.coilSeries[:, :, :])
theta = np.linspace(0, 2 * np.pi, 32 + 1)
l = r(fc, theta)
mlab.clf()
q = draw_surface(r_surf)
q = draw_coils(l)

with tb.open_file("coils_force.hdf5", "r") as f:
    fc = np.asarray(f.root.coilSeries[:, :, :])
theta = np.linspace(0, 2 * np.pi, 32 + 1)
l = r(fc, theta)
q = draw_coils_c(l, c=(1, 1, 1))
q